In [1]:
import platform
if 'mac' in platform.platform():
    BASE_DIR = "/Users/USER/vrtopc/"
    DATA_DIR = "/media/data/vrtopc"
else:
    BASE_DIR = "/home/USER/vrtopc/"
    DATA_DIR = "/media/data/vrtopc"

import sys
sys.path.append(BASE_DIR)

## Imports

In [2]:
import numpy as np
import cv2
import time

import os

import matplotlib.pyplot as plt
%matplotlib inline

## Parameters

In [3]:
ENV_SAMPLING_DATA = False

SEED = 1
ENVIRONMENT = 'box_messy'
BEHAVIOUR_SCHEME = 'adult'

ENV_DIM = 0.635
FPS = 10
SECONDS = 720

VIEWING_SECONDS = 30
TAIL_LENGTH = 150

## Movie

In [4]:
ENV_SHAPE = ENVIRONMENT.split('_')[0]
EXPERIMENT_DIR = os.path.join(
    DATA_DIR, ENV_SHAPE, BEHAVIOUR_SCHEME,
    f"exp_dim{ENV_DIM}_fps{FPS}_s{SECONDS}_seed{SEED:02d}"
)
if ENV_SAMPLING_DATA:
    EXPERIMENT_DIR = os.path.join(
        DATA_DIR,
        ENV_SHAPE,
        "env_sampling"
    )
print(EXPERIMENT_DIR)


/media/data/vrtopc/box/adult/exp_dim0.635_fps10_s720_seed01


In [5]:
import yaml
with open(os.path.join(EXPERIMENT_DIR, "config.yaml")) as f:
    config = yaml.safe_load(f)

FRAME_DIM = config['FRAME_DIM']

In [6]:
riab_dir = os.path.join(EXPERIMENT_DIR, "riab_simulation")

positions = np.load(os.path.join(riab_dir, "positions.npy"))
thetas = np.load(os.path.join(riab_dir, "thetas.npy"))
velocities = np.load(os.path.join(riab_dir, "velocities.npy"))

In [7]:
video_dir = os.path.join(EXPERIMENT_DIR, ENVIRONMENT)

files = sorted(
    [os.path.join(video_dir, f) for f in os.listdir(video_dir) if os.path.isfile(os.path.join(video_dir, f))]
)

video = np.zeros((FRAME_DIM[1], FRAME_DIM[0], len(files)), dtype=np.float64)

for idx, f in enumerate(files):
    im = cv2.imread(f, cv2.IMREAD_GRAYSCALE)
    video[:,:,idx] = im.astype(np.float64) / 255

In [8]:
positions.shape, velocities.shape, video.shape

((7200, 2), (7200, 2), (64, 128, 7200))

In [9]:
N_FRAMES = FPS*VIEWING_SECONDS

# np.random.seed(SEED)
START_FRAME = np.random.randint(0, video.shape[-1]-N_FRAMES)
END_FRAME = START_FRAME + N_FRAMES

print(START_FRAME, END_FRAME)

1270 1570


In [10]:
start = time.time()
from matplotlib import animation
from IPython import display

alpha = np.linspace(0, 1, TAIL_LENGTH+1)

fig, ax = plt.subplots(figsize=(8, 8))
ax.set_xticks([])
ax.set_yticks([])
ax.set_xlim([0, ENV_DIM])
ax.set_xlim([0, ENV_DIM])
ax.set_ylim([0, ENV_DIM])
sc = ax.scatter(
    positions[max(START_FRAME-TAIL_LENGTH, 0):START_FRAME+1, 0],
    positions[max(START_FRAME-TAIL_LENGTH, 0):START_FRAME+1, 1],
    c=['b']*TAIL_LENGTH+['r'], s=[1e2]*TAIL_LENGTH+[4e2], alpha=alpha
)

plt.close() # this is required to not display the generated image

def init():
    sc.set_offsets(np.stack(
        [positions[max(START_FRAME-TAIL_LENGTH, 0):START_FRAME+1, 0],
        positions[max(START_FRAME-TAIL_LENGTH, 0):START_FRAME+1, 1]],
        axis=1
    ))

def animate(i):
    idx = START_FRAME+i
    sc.set_offsets(np.stack(
        [positions[max(idx-TAIL_LENGTH, 0):idx+1, 0],
        positions[max(idx-TAIL_LENGTH, 0):idx+1, 1]],
        axis=1
    ))

    return sc

anim = animation.FuncAnimation(
    fig,
    animate,
    init_func=init,
    frames=END_FRAME-START_FRAME,
    interval=1_000/FPS # ms
)

# anim.save(f"{BEHAVIOUR_SCHEME}.mp4")

# with open("animation.html", "w") as f:
#     print(anim.to_html5_video(), file=f)

html_video = display.HTML(anim.to_html5_video())

end = time.time()

dt = end-start
display.display(html_video)
print(f"Elapsed time {dt:.2f}")

Elapsed time 2.92


In [12]:
start = time.time()
from matplotlib import animation
from IPython import display

alpha = np.linspace(0.1, 1, 10)

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(22, 8), width_ratios=[1.25, 2])
ax1.set_xticks(np.arange(0, ENV_DIM+0.05, 0.1), np.round(np.arange(0, ENV_DIM+0.05, 0.1),1), fontsize=24)
ax1.set_yticks(np.arange(0.1, ENV_DIM+0.05, 0.1), np.round(np.arange(0.1, ENV_DIM+0.05, 0.1),1), fontsize=24)
ax1.set_xlim([0, ENV_DIM])
ax1.set_ylim([0, ENV_DIM])
sc = ax1.scatter(
    positions[max(START_FRAME-9, 0):START_FRAME+1, 0],
    positions[max(START_FRAME-9, 0):START_FRAME+1, 1],
    c=['b']*9+['r'], s=[1e2]*9+[2e2], alpha=alpha
)

im = ax2.imshow(video[:,:,START_FRAME], cmap='gray')

plt.axis('off')

plt.close() # this is required to not display the generated image

def init():
    sc.set_offsets(np.stack(
        [positions[max(START_FRAME-9, 0):START_FRAME+1, 0],
        positions[max(START_FRAME-9, 0):START_FRAME+1, 1]],
        axis=1
    ))
    # sc.set_alphas(alpha)

    # for idx in range(max(START_FRAME-9, 0), START_FRAME+1):
    #     patch = plt.Arrow(
    #         positions[idx, 0],
    #         positions[idx, 1],
    #         velocities[idx+1, 0]/FPS/2,
    #         velocities[idx+1, 1]/FPS/2,
    #         width=1e-8,
    #         color='red',
    #         alpha=alpha[idx-(max(START_FRAME-9, 0))],
    #         zorder=5
    #     )
    #     ax1.add_patch(patch)

    im.set_data(video[:,:,START_FRAME])

def animate(i):
    idx = START_FRAME+i
    sc.set_offsets(np.stack(
        [positions[max(idx-9, 0):idx+1, 0],
        positions[max(idx-9, 0):idx+1, 1]],
        axis=1
    ))
    # sc.set_alphas(alpha)

    # ax1.patches[0].remove()
    # for j in range(0, 9):
    #     ax1.patches[j].set_alpha(alpha[j])
    # patch = plt.Arrow(
    #     positions[idx, 0],
    #     positions[idx, 1],
    #     velocities[idx+1, 0]/FPS/2,
    #     velocities[idx+1, 1]/FPS/2,
    #     width=1e-8,
    #     color='red',
    #     alpha=alpha[-1],
    #     zorder=5
    # )
    # ax1.add_patch(patch)

    im.set_data(video[:,:,idx])
    return im

anim = animation.FuncAnimation(
    fig,
    animate,
    init_func=init,
    frames=END_FRAME-START_FRAME,
    interval=1_000/FPS # ms
)

# anim.save("animation.mp4")

# with open("animation.html", "w") as f:
#     print(anim.to_html5_video(), file=f)

html_video = display.HTML(anim.to_html5_video())

end = time.time()

dt = end-start
display.display(html_video)
print(f"Elapsed time {dt:.2f}")

Elapsed time 16.38
